In [17]:
import pickle
import pandas as pd
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from datasets import Dataset

In [18]:
with open(
        "/workspace/Emotion_Intent_Chat/JEmpatheticDialogue/JEmpatheticDialogue_all.pkl",
        "rb",
) as f:
    conversation_list = pickle.load(f)

In [19]:
print(conversation_list[0])

[{'role': 'user', 'content': '寝ているときに首がもぞもぞしたので、起きて見てみたらムカデがいたの！'}, {'role': 'assistant', 'content': 'きゃーっ！それはびっくりだね。'}, {'role': 'user', 'content': 'そうなのよ。時々ムカデ出るんだよね。でも寝ているときに来なくても。'}, {'role': 'assistant', 'content': '聞いているだけでも鳥肌が立ってきた。'}]


In [20]:
dic = {"conversation": [], "human_response": [], "last_user_input": []}

In [21]:
for conversation_set in tqdm(conversation_list):
    history_str = f'ユーザ：「{conversation_set[0]["content"]}」\nシステム応答：「{conversation_set[1]["content"]}」\nユーザ：「{conversation_set[2]["content"]}」\nシステム：「？？？」'
    response = conversation_set[3]["content"]
    last_user_input = conversation_set[2]["content"]
    dic["conversation"].append(history_str)
    dic["human_response"].append(response)
    dic["last_user_input"].append(last_user_input)

100%|██████████| 20000/20000 [00:00<00:00, 565647.43it/s]


In [22]:
print(dic)

{'conversation': ['ユーザ：「寝ているときに首がもぞもぞしたので、起きて見てみたらムカデがいたの！」\nシステム応答：「きゃーっ！それはびっくりだね。」\nユーザ：「そうなのよ。時々ムカデ出るんだよね。でも寝ているときに来なくても。」\nシステム：「？？？」', 'ユーザ：「車同士がぶつかる瞬間を見てしまいました。」\nシステム応答：「まあ。あなたは大丈夫だったの？」\nユーザ：「私は大丈夫でした。でも音と衝撃が凄かったですよ。」\nシステム：「？？？」', 'ユーザ：「先日、うちの子が学校の帰りに体調悪くて座り込んでたおじいさんを助けて表彰されたんだ。」\nシステム応答：「それはすごいわね！\u3000しっかりしたお子さんなのね。」\nユーザ：「親バカかもしれないけれど、表彰されたというより、そういう行動ができたことが親として誇りに思うよ。」\nシステム：「？？？」', 'ユーザ：「この間一人で焼肉屋さんに行ったんですけど、寂しくてあまり楽しくありませんでした。」\nシステム応答：「一人焼肉はあまり好きではないんですか？」\nユーザ：「そうですね、私はどちらかというとみんなと賑やかに食べる方が好きです。」\nシステム：「？？？」', 'ユーザ：「先週、車を買ったんです。」\nシステム応答：「国産車ですか？」\nユーザ：「外車なんです。高価なので気をつけて乗っていたんですが、買った次の日にぶつけられてしまって。相手に激怒してしまいました。」\nシステム：「？？？」', 'ユーザ：「最近胸のあたりが痛い事が多いんだよ。」\nシステム応答：「なんかの病気かもしれないね。」\nユーザ：「そうなんだよ、大きな病気にかかっていたらどうしようって不安に思っている。」\nシステム：「？？？」', 'ユーザ：「転校してしばらく会えなかった友達と会うことになったんだ。」\nシステム応答：「それは久々の再会だね。」\nユーザ：「ずっと顔を見ていなかったから楽しみすぎて待ち切れない。」\nシステム：「？？？」', 'ユーザ：「初めてクラブに来たよ。」\nシステム応答：「クラブってどんな感じなの？」\nユーザ：「めちゃくちゃ上がる音楽が流れていて可愛い子もいっぱいいて最高に楽しい。」\nシステム：「？？？」', 'ユーザ：「一回だけ行ったことのあるキャバクラの前を通りがか

In [23]:
df = pd.DataFrame(dic)
df.to_excel("df_human_output.xlsx", index=False)

In [24]:
seed = 0

# Split the dataset
train_df, val_test_df = train_test_split(df, test_size=0.05, random_state=seed)
val_df, test_df = train_test_split(val_test_df, test_size=0.5, random_state=seed)

train_ds = Dataset.from_pandas(train_df)
val_ds = Dataset.from_pandas(val_df)
test_ds = Dataset.from_pandas(test_df)

train_ds.set_format(type="torch")
val_ds.set_format(type="torch")
test_ds.set_format(type="torch")

In [25]:
print(test_ds[0])

{'conversation': 'ユーザ：「今日は朝から夕方まで、姪っ子がうちに来てたんです。」\nシステム応答：「それは大変でしたね。」\nユーザ：「いえいえ、大変じゃなくて、大満足ですよ。たくさん遊べましたから。」\nシステム：「？？？」', 'human_response': '可愛がってるんですねえ。', 'last_user_input': 'いえいえ、大変じゃなくて、大満足ですよ。たくさん遊べましたから。', '__index_level_0__': tensor(4313)}


In [26]:
with open("all_turns_test.pkl", "wb") as f:
    pickle.dump(test_ds, f)